# Pipeline 1
+ knowledge base
+ training
+ evaluation
+ vector database
+ rag

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
!pip install python-dotenv

In [3]:
from dotenv import load_dotenv
load_dotenv("/content/drive/Shareddrives/Knowledge Graph/code/pipeline/.env", override=True)

True

## Knowledge base
In this component we perform the loading of the knowledge base

In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/0.knowledge_base
!pip install -r requirements.txt

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/0.knowledge_base
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 567.0/567.0 kB 12.3 MB/s eta 0:00:00


In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/files

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/files


In [ ]:
import os
import random
import pickle
import rdflib

def knowledge_base():
    def parse_rdf(file_path):
        g = rdflib.Graph()
        try:
            g.parse(file_path, format='ttl')
        except rdflib.exceptions.ParserError as e:
            print(f"Errore di parsing: {e}")
        triples = [(str(s), str(p), str(o)) for s, p, o in g]
        return triples

    input_path = os.getenv('input_path')
    output_path = os.getenv('output_path')

    rdf_triples = parse_rdf(input_path)

    random.shuffle(rdf_triples)
    num_triples = len(rdf_triples)
    train_size = int(0.8 * num_triples)
    valid_size = int(0.1 * num_triples)
    test_size = num_triples - train_size - valid_size

    train_triples = rdf_triples[:train_size]
    valid_triples = rdf_triples[train_size:train_size + valid_size]
    test_triples = rdf_triples[train_size + valid_size:]

    print(f'Number of triples in the training set: {len(train_triples)}')
    print(f'Number of triples in the validation set: {len(valid_triples)}')
    print(f'Number of triples in the test set: {len(test_triples)}')

    with open(output_path, 'wb') as f:
        pickle.dump((train_triples, valid_triples, test_triples), f)

if __name__ == "__main__":
    knowledge_base()


Number of triples in the training set: 25048
Number of triples in the validation set: 3131
Number of triples in the test set: 3131


## Training
In this component we perform the training of a knowledge graph embedding model (e.g. TransE) on the knowledge base loaded previously

In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/1.training
!pip install -r requirements.txt

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/1.training
  Cloning https://github.com/pykeen/pykeen.git to /tmp/pip-req-build-ly_9rhql
  Running command git clone --filter=blob:none --quiet https://github.com/pykeen/pykeen.git /tmp/pip-req-build-ly_9rhql
  Resolved https://github.com/pykeen/pykeen.git to commit 0eb14895ebc5d803f268fa23a0b5504a255ca3a9
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/files

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/files


### Training with dataset from file

In [ ]:
import os
import torch
from pykeen.datasets import PathDataset
from pykeen.pipeline import pipeline
from pykeen.evaluation import RankBasedEvaluator
from pykeen.losses import MarginRankingLoss
from pykeen.trackers import TensorBoardResultTracker
from pykeen.models import TransE
from pykeen.training import SLCWATrainingLoop
from pykeen.sampling import BasicNegativeSampler
from pykeen.triples import TriplesFactory
import pykeen.models
import pickle
import numpy as np


def train():
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    print(f"Using device: {device}")
    embedding_dim = int(os.getenv('EMBEDDING_DIM'))
    num_epochs = int(os.getenv('NUM_EPOCHS'))
    learning_rate = float(os.getenv('LEARNING_RATE'))
    num_negs_per_pos = int(os.getenv('NUM_NEGS_PER_POS'))
    model_name = os.getenv('MODEL')
    training_loop = os.getenv('TRAINING_LOOP')
    optimizer = os.getenv('OPTIMIZER')

    with open(os.getenv('output_path_arch'), 'rb') as f:
        train_triples, valid_triples, test_triples = pickle.load(f)

    all_triples = train_triples + valid_triples + test_triples
    train_triples_np = np.array(all_triples)
    train_tf = TriplesFactory.from_labeled_triples(train_triples_np)

    tracker = TensorBoardResultTracker(experiment_path=os.getenv('TENSORBOARD_PATH_ARCH'), experiment_name=model_name)

    model_class = getattr(pykeen.models, model_name)

    model = model_class(
        triples_factory=train_tf,
        embedding_dim=embedding_dim,
        random_seed=42,
        loss="MarginRankingLoss",

        ).to(device)
    negative_sampler = BasicNegativeSampler(
        mapped_triples = train_tf.mapped_triples,
        num_negs_per_pos=num_negs_per_pos)

    training_loop = SLCWATrainingLoop(
        triples_factory=train_tf,
        model = model,
        optimizer=optimizer,
        optimizer_kwargs=dict(lr=learning_rate),
        result_tracker = tracker,
        negative_sampler = negative_sampler,
    )

    checkpoint_directory = './training'
    checkpoint_frequency = 10

    training_loop.train(
        triples_factory=train_tf,
        num_epochs = num_epochs,
        checkpoint_name = os.getenv('CHECKPOINT_NAME_ARCH'),
        checkpoint_directory=checkpoint_directory,
        batch_size=1024,
        checkpoint_frequency=checkpoint_frequency,
    )

    model_path = os.getenv('MODEL_PATH_ARCH')
    with open(model_path, 'wb') as file:
      pickle.dump(model, file)

    return model

if __name__ == "__main__":
    model = train()

INFO:pykeen.nn.representation:Inferred unique=False for Embedding()
INFO:pykeen.nn.representation:Inferred unique=False for Embedding()
INFO:pykeen.training.training_loop:=> no checkpoint found at 'training/checkpoint_arch.pt'. Creating a new file.


Using device: cuda


Training epochs on cuda:0:   0%|          | 0/580 [00:00<?, ?epoch/s]

Training batches on cuda:0:   0%|          | 0/1 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/1 [00:00<?, ?batch/s]

...

Training batches on cuda:0:   0%|          | 0/1 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/1 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/1 [00:00<?, ?batch/s]

Training batches on cuda:0:   0%|          | 0/1 [00:00<?, ?batch/s]

INFO:pykeen.training.training_loop:=> Saved checkpoint after having finished epoch 580.


## Evaluation
In this component we perform the evaluation of the trained model

In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/2.evaluation
!pip install -r requirements.txt

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/2.evaluation
  Cloning https://github.com/pykeen/pykeen.git to /tmp/pip-req-build-368t8ngi
  Running command git clone --filter=blob:none --quiet https://github.com/pykeen/pykeen.git /tmp/pip-req-build-368t8ngi
  Resolved https://github.com/pykeen/pykeen.git to commit 0eb14895ebc5d803f268fa23a0b5504a255ca3a9
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/files

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/files


### Evaluation with dataset from file

In [ ]:
import json
import torch
import os
import pickle
from pykeen.evaluation import RankBasedEvaluator
from pykeen.triples import TriplesFactory
import pykeen.models

def evaluate():
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    print(f"Using device: {device}")

    model_name = os.getenv('MODEL')
    model_path = os.getenv('MODEL_PATH')

    model_class = getattr(pykeen.models, model_name)
    with open(model_path, 'rb') as file:
        model = pickle.load(file)
    model = model.to(device)

    with open(os.getenv('output_path'), 'rb') as f:
        train_triples, valid_triples, test_triples = pickle.load(f)


    train_triples_np = np.array(train_triples)
    valid_triples_np = np.array(valid_triples)
    test_triples_np = np.array(test_triples)
    train_tf = TriplesFactory.from_labeled_triples(train_triples_np)
    valid_tf = TriplesFactory.from_labeled_triples(valid_triples_np)
    test_tf = TriplesFactory.from_labeled_triples(test_triples_np)

    evaluator = RankBasedEvaluator(
        metrics=["hits_at_k"],
        metrics_kwargs=[dict(k=100)],
        filtered=True)

    additional_filter_triples = [
        train_tf.mapped_triples,
        test_tf.mapped_triples,
    ]

    validation_results = evaluator.evaluate(
        model=model,
        mapped_triples=valid_tf.mapped_triples,
        additional_filter_triples=additional_filter_triples,
    )

    selected_validation_metrics = {
    'hits@1': validation_results.get_metric('hits@1'),
    'hits@3': validation_results.get_metric('hits@3'),
    'hits@5': validation_results.get_metric('hits@5'),
    'hits@10': validation_results.get_metric('hits@10'),
    'hits@100': validation_results.get_metric('hits@100'),
    'MRR': validation_results.get_metric('mean_reciprocal_rank')
    }


    validation_results_path = os.getenv('VALIDATION_RESULTS_PATH')
    with open(validation_results_path, 'w') as f:
        json.dump(selected_validation_metrics, f, indent=4)

    print(f"Validation results saved to {validation_results_path}")

    additional_filter_triples = [
        train_tf.mapped_triples,
        valid_tf.mapped_triples,
    ]

    test_results = evaluator.evaluate(
        model=model,
        mapped_triples=test_tf.mapped_triples,
        additional_filter_triples=additional_filter_triples,
    )

    selected_test_metrics = {
    'hits@1': test_results.get_metric('hits@1'),
    'hits@3': test_results.get_metric('hits@3'),
    'hits@5': test_results.get_metric('hits@5'),
    'hits@10': test_results.get_metric('hits@10'),
    'hits@100': test_results.get_metric('hits@100'),
    'MRR': test_results.get_metric('mean_reciprocal_rank')
    }

    test_results_path = os.getenv('TEST_RESULTS_PATH')
    with open(test_results_path, 'w') as f:
        json.dump(selected_test_metrics, f, indent=4)

    print(f"Test results saved to {test_results_path}")

if __name__ == "__main__":
    evaluate()


Using device: cuda


Evaluating on cuda:0:   0%|          | 0.00/3.13k [00:00<?, ?triple/s]

INFO:pykeen.evaluation.evaluator:Evaluation took 8.92s seconds


Validation results saved to ./evaluation/validation_results_TransE_d3fend.txt


Evaluating on cuda:0:   0%|          | 0.00/3.13k [00:00<?, ?triple/s]

INFO:pykeen.evaluation.evaluator:Evaluation took 8.88s seconds


Test results saved to ./evaluation/test_results_TransE_hetionet_250ep.txt


## Vector database
In this component we perform the loading of the embeddings extracted from the trained model in the vector database Weaviate.

In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/3.vector_database
!pip install -r requirements.txt

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/3.vector_database
  Cloning https://github.com/pykeen/pykeen.git to /tmp/pip-req-build-agio7l70
  Running command git clone --filter=blob:none --quiet https://github.com/pykeen/pykeen.git /tmp/pip-req-build-agio7l70
  Resolved https://github.com/pykeen/pykeen.git to commit 0eb14895ebc5d803f268fa23a0b5504a255ca3a9
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 325.4/325.4 kB 13.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.5/43.5 kB 3.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 223.8/223.8 kB 19.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 57.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 364.4/364.4 kB 27.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.5/233.5 kB 18.9 MB/s eta 0:00:00
   ━━━━━━━━━━

In [ ]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/files

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/files


### Vector database with database from file

In [ ]:

import re
import torch
import time
import os
import numpy as np
import json
import pykeen.models
import pandas as pd
import pickle

# Funzione per estrarre l'ultima parte dell'URL
def extract_name(url):
    return re.split(r'[#/]', url)[-1]

# Funzione per normalizzare i vettori
def normalize_vector(v):
    return v / np.linalg.norm(v)

# Funzione per scrivere i dati su file JSON
def write_to_file(filename, data):
    with open(filename, 'w') as file:
        json.dump(data, file, indent=4)

def embeddings():
  device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
  print(f"Using device: {device}")

  model_name = os.getenv('MODEL')
  model_path = os.getenv('MODEL_PATH_ARCH')

  model_class = getattr(pykeen.models, model_name)
  with open(model_path, 'rb') as file:
      model = pickle.load(file)
  model = model.to(device)

  entity_embeddings = model.entity_representations[0](indices=None)
  relation_embeddings = model.relation_representations[0](indices=None)

  entity_embeddings_cpu = entity_embeddings.detach().cpu()
  relation_embeddings_cpu = relation_embeddings.detach().cpu()

  entity_embeddings_list = entity_embeddings_cpu.numpy().tolist()
  relation_embeddings_list = relation_embeddings_cpu.numpy().tolist()


  with open(os.getenv('output_path_arch'), 'rb') as f:
      train_triples, valid_triples, test_triples = pickle.load(f)
  all_triples = train_triples+valid_triples+test_triples
  all_triples_np = np.array(all_triples)
  from pykeen.triples import TriplesFactory
  triples_factory = TriplesFactory.from_labeled_triples(all_triples_np)

  entity_to_id = triples_factory.entity_to_id
  relation_to_id = triples_factory.relation_to_id

  entity_embeddings_dict = {entity: entity_embeddings_list[idx] for entity, idx in entity_to_id.items()}
  relation_embeddings_dict = {relation: relation_embeddings_list[idx] for relation, idx in relation_to_id.items()}

  entities_json = []
  for entity_name, embedding in entity_embeddings_dict.items():
      entity_data = {
          "name": extract_name(entity_name),
          "embedding": embedding,
          "source": extract_name(entity_name),

      }
      entities_json.append(entity_data)

  # Scrivere i dati delle entità su file JSON
  write_to_file('./vector_database/entity_embeddings_arch.json', entities_json)

  relations_json = []
  for relation_name, embedding in relation_embeddings_dict.items():
      relation_data = {
          "name": extract_name(relation_name),
          "embedding": embedding,
          "source": extract_name(relation_name)
      }
      relations_json.append(relation_data)
  # Scrivere i dati delle relazioni su file JSON
  write_to_file('./vector_database/relation_embeddings_arch.json', relations_json)

  print("Entity and relation embeddings have been saved to JSON files.")

if __name__ == "__main__":
    embeddings()


Using device: cuda
Entity and relation embeddings have been saved to JSON files.


## RAG
In this component we perform a Retrieval Augmented Generation from the data loaded in Weaviate

In [4]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/4.rag
!pip install -r requirements.txt

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/4.rag
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 43.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 325.4/325.4 kB 25.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.5/43.5 kB 3.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.2/54.2 kB 5.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 223.8/223.8 kB 18.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.5/2.5 MB 64.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 519.1/519.1 kB 32.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 54.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 49.6/49.6 kB 4.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 319.7/319.7 kB 24.3 MB/s eta 0:00:00
  Attempting uninstall: protobuf
    Found existing installation: protobuf 4.25.5
    Uninstalling protobuf-4.25.5:
      Successfully uninstalled 

In [5]:
%cd /content/drive/Shareddrives/Knowledge Graph/code/pipeline/files

/content/drive/Shareddrives/Knowledge Graph/code/pipeline/files


In [7]:
import os
from langchain_openai import ChatOpenAI
from langchain_openai import OpenAIEmbeddings
import textwrap
import numpy as np
from numpy.linalg import norm
import json

def rag():
    # Funzione per caricare i dati JSON
    def load_embeddings(file_path):
        with open(file_path, 'r') as file:
            return json.load(file)

    def cosine_similarity(A, B):
        return np.dot(A,B)/(norm(A)*norm(B))


    # Funzione per fare la similarity search
    def similarity_search(question):
        # Carica gli embedding dal file JSON
        embeddings_data = load_embeddings("./vector_database/entity_embeddings_arch.json")
        embeddings_data.extend(load_embeddings("./vector_database/relation_embeddings_arch.json"))

        embedding_model = OpenAIEmbeddings(
            api_key=os.getenv("OPENAI_API_TOKEN"),
            model="text-embedding-ada-002",
        )
        query_vector = embedding_model.embed_query(question)

        # Calcola la similarità per ciascun embedding
        similarities = []
        for entry in embeddings_data:
            entity_name = entry['name']
            embedding = np.array(entry['embedding'])
            similarity = cosine_similarity(query_vector, embedding)
            similarities.append((entity_name, similarity))

        # Ordina per similarità decrescente
        similarities.sort(key=lambda x: x[1], reverse=True)

        # Restituisci i top_k risultati
        return similarities[:5]

    # Funzione per generare una risposta dal modello LLM
    def generate_RAG_answer(question: str, context: str):
        llm = ChatOpenAI(
            temperature=0,
            api_key=os.getenv("OPENAI_API_TOKEN"),
            model_name="gpt-3.5-turbo"
        )
        prompt = f"Answer the question based on the context: \n\nContext: {context}\n\nQuestion: {question}"
        response = llm.invoke(prompt)
        return response.content

        # Funzione per generare una risposta dal modello LLM
    def generate_LLM_answer(question: str):
        llm = ChatOpenAI(
            temperature=0,
            api_key=os.getenv("OPENAI_API_TOKEN"),
            model_name="gpt-3.5-turbo"
        )
        response = llm.invoke(question)
        return response.content

    # Funzione per stampare i risultati in un formato leggibile
    def pretty_print_response(question: str):
        print(f"Question: {question}")
        print("=" * 90)
        print("Similarity Search Results:")
        context = similarity_search(question)
        print(context)
        print("=" * 90)
        # Genera la risposta basata sul contesto
        answer = generate_RAG_answer(question, context)
        print("=" * 90)
        print("RAG Answer:")
        print(textwrap.fill(answer, 60))
        print("=" * 90)
        print("LLM Answer:")
        print(textwrap.fill(generate_LLM_answer(question), 60))
        print("=" * 90)

    question = "What does the user do in my architecture?"
    pretty_print_response(question)
    print("--------------------------------------------------------------------------------------")
    question2 = "How many types of mail servers do I have in my architecture?"
    pretty_print_response(question2)
    print("--------------------------------------------------------------------------------------")
    question3 = "Which mail server retrieves emails for the user?"
    pretty_print_response(question3)
    print("--------------------------------------------------------------------------------------")
    question4 = "Is IMAP used for retrieving emails?"
    pretty_print_response(question4)


if __name__ == "__main__":
    rag()

Question: What does the user do in my architecture?
Similarity Search Results:
[('Database', 0.06392158012694271), ('type', 0.03391174367394687), ('SMTP Server', 0.029271359420944672), ('MailDatabase', 0.014087258747387886), ('VerifiesCredentials', 0.01326458609354354)]
RAG Answer:
The user verifies credentials in the architecture.
LLM Answer:
In your architecture, the user interacts with the system by
inputting commands, requests, or data through the user
interface. The user's actions trigger processes within the
system, such as data processing, communication with external
systems, or generating outputs. The user may also receive
feedback, notifications, or results from the system based on
their interactions. Overall, the user plays a crucial role
in driving the functionality and behavior of the
architecture.
--------------------------------------------------------------------------------------
Question: How many types of mail servers do I have in my architecture?
Similarity Search Re